# Spire Attitude State Vectors

Raw Spire Data: from longterm attitude file
 - filename: `\20180923_20181209_TaskOrder3Data/leoAtt_2018-09-23T00-12-00Z.9999999.083.log`  
 
 - Position and Velocity frame: `ECI-TEME of epoch`

 - quaternions rotation: `SBF-->RSW`  
 - GEODYN required quaternion rotation: `SBF-->J2000`  


# View the initial conditions

In [24]:
import pandas as pd
epoch_start = "2018-11-09 00:00:00"


prms_arc={}
prms_arc['epoch_start'] = epoch_start
prms_arc['epoch_startDT'] = pd.to_datetime(prms_arc['epoch_start'],\
                                            format='%Y-%m-%d %H:%M:%S')

epoch_startDT = prms_arc['epoch_startDT']
file_statevector_ICs = "/data/SatDragModelValidation/data/inputs/sat_spire83/setups/statevector_ICs_eci.txt"

datetype = 'datetime_string'

date_in_file_flag= False
import linecache

### Only need to use accuracy to within 1 second (ignore the microseconds in the file)

if datetype == 'datetime_string':
    date_str = str(epoch_startDT)
elif datetype == 'YYMMDDHHMMSS':
    date_str = datetime.strftime(epoch_startDT, '%y%m%d%H%M%S')


with open(file_statevector_ICs, 'r') as f:
    for line_no, line_text in enumerate(f):
        if date_str in line_text:
            date_in_file_flag= True
            print('    ','xyzline',line_no,line_text)
            break
if date_in_file_flag == False:

    ### Find the dates that have the same hour    
    if datetype == 'datetime_string':
        date_roundhour_str = str(epoch_startDT)[:10]
    elif datetype == 'YYMMDDHHMMSS':
        date_roundhour_str = datetime.strftime(epoch_startDT, '%y%m%d%H%M%S')

    ### Scan through IC file and append a list of dates within the same hour
    line_no_list = []
    line_list = []
    with open(file_statevector_ICs, 'r') as f:
        for line_no, line_text in enumerate(f):
            if date_roundhour_str in line_text:
                line_no_list.append(line_no)
    for i in np.arange(line_no_list[0]-10, line_no_list[-1]+10):
        line = linecache.getline(file_statevector_ICs,i)
        line_list.append(line)
    dates = []
    for i ,val in enumerate(line_list):
        if datetype == 'datetime_string':
            dates.append(pd.to_datetime(line_list[i][:19],format='%Y-%m-%d %H:%M:%S'))
        elif datetype == 'YYMMDDHHMMSS':
            dates.append(pd.to_datetime(line_list[i][:19],format='%y%m%d%H%M%S.%f'))
            
            
            
xyzline = pd.read_csv(file_statevector_ICs, 
            skiprows = 255662, 
            nrows=line_no_list[-1]- line_no_list[0],           
            sep = '\s+',
            dtype=object,
            names = [
                'DateYMD',
                'DateHMS',
                'X',
                'Y',
                'Z',
                'X_dot',
                'Y_dot',
                'Z_dot',
                    ],)

xyzline['Date'] =  pd.to_datetime(xyzline['DateYMD']+xyzline['DateHMS'], format='%Y-%m-%d%H:%M:%S')
del xyzline['DateYMD'], xyzline['DateHMS']





import plotly.graph_objects as go
from plotly.offline import plot, iplot
from plotly.subplots import make_subplots
import plotly.express as px

config = dict({
                'displayModeBar': True,
                'responsive': False,
                'staticPlot': True,
                'displaylogo': False,
                'showTips': False,
                })


fig = make_subplots(rows=3, cols=1)

fig.add_trace(go.Scattergl(
            x=pd.to_datetime(xyzline['Date']),
            y=xyzline['X'].values.astype(float),
                mode='markers',
                opacity=1,
                marker=dict(size=3),
                showlegend=False),
                secondary_y=False, row=1, col=1,)

fig.add_trace(go.Scattergl(
            x=pd.to_datetime(xyzline['Date']),
            y=xyzline['Y'].values.astype(float),
                mode='markers',
                opacity=1,
                marker=dict(size=3),
                showlegend=False),
                secondary_y=False, row=2, col=1,)

fig.add_trace(go.Scattergl(
            x=pd.to_datetime(xyzline['Date']),
            y=xyzline['Z'].values.astype(float),
                mode='markers',
                opacity=1,
                marker=dict(size=3),     
                showlegend=False),
                secondary_y=False, row=3, col=1,)


fig.update_layout(
        autosize=True
#         width=800,height=900,
                )
fig.show(config=config)




2018-11-09 00:00:00 not found in file. 


In [25]:
xyzline['Date']

0       2018-11-09 00:05:35
1       2018-11-09 00:05:36
2       2018-11-09 00:05:37
3       2018-11-09 00:05:38
4       2018-11-09 00:05:39
                ...        
30001   2018-11-09 23:59:54
30002   2018-11-09 23:59:55
30003   2018-11-09 23:59:56
30004   2018-11-09 23:59:57
30005   2018-11-09 23:59:58
Name: Date, Length: 30006, dtype: datetime64[ns]

In [ ]:
import os
import numpy    as np
from   datetime import datetime
from   pandas   import isnull      as pd_isnull
from   pandas   import Timestamp   as pd_Timestamp
from   pandas   import to_datetime as pd_to_datetime
import gc

## Load Spire POD

In [ ]:
dir_spire = '/data/SatDragModelValidation/data/inputs/sat_spire83/data_Spire/arcs'

file_IC = '/data/SatDragModelValidation/data/inputs/sat_spire83/setups/statevector_ICs_eci.txt'


spire_sat_num = 83
days          = np.arange(1,32)
# days          = [7,8,9,10,11]#np.arange(1,3)


In [ ]:
## This is too slow.
#     - 

In [ ]:
#### Find the files in the directories that contain the Satellite's LeoOrb POD.
files_with_sat = []
## Loop through the daily directories
for iday,day in enumerate(days):
    dir_set   = dir_spire + f'/2018-11-{day:02d}/'
    
    ## Loop through the arc directories for that day,
    ## Identify the leoOrb..._{sat#}.sp3 (Spire "POD") files
    for root, dirs, files in os.walk(dir_set, topdown=False):
        for name in files:
            if 'leoOrb'in name and f'{spire_sat_num:03d}.sp3' in name:
                files_with_sat.append(os.path.join(root, name))

del root, dirs, files, name
del days, iday, day

In [ ]:
from pygeodyn.satellite_spire import read_SpireLeoOrbPOD_sp3c

leoOrb_ecef = read_SpireLeoOrbPOD_sp3c(files_with_sat)
del files_with_sat
gc.collect()

## Convert ECEF (IGS08) to ECI (J2000)


In [ ]:
import numpy  as np
import pandas as pd
from  datetime import datetime,timedelta
import os

## Load coordinate transformation function
from pygeodyn.util_dir.coordinate_systems import iau06_Call_ecef2eci

Convert GPS time to UTC


In [ ]:
from pygeodyn.util_dir.time_systems import time_gps_to_utc,\
                                           get_leapseconds,\
                                           jday
### get the leapseconds for time of interest
jd, jdfrac = jday(leoOrb_ecef['date_gps'][0].year,
                  leoOrb_ecef['date_gps'][0].month,
                  leoOrb_ecef['date_gps'][0].day,
                  0,0,0)
dAT = get_leapseconds(jd+jdfrac-2400000.5)



leoOrb_ecef['date_utc'] = [time_gps_to_utc(time, dAT) \
                              for time in leoOrb_ecef['date_gps']]
del leoOrb_ecef['date_gps']
del leoOrb_ecef['clock_microsec']


gc.collect()

Convert all ephems from ecef to eci

In [ ]:
print(leoOrb_ecef.keys())
print(len(leoOrb_ecef['date_utc']))

In [ ]:
# import cProfile, pstats, io
# from pstats import SortKey

# pr = cProfile.Profile()
# pr.enable()
import time
start = time.time()


conv_dms2kms = 1/10000.
#
len_ecef = np.shape(leoOrb_ecef['date_utc'])[0]
#
# leoOrb_eci = {}
# leoOrb_eci['x_km']     = np.zeros(len_ecef)
# leoOrb_eci['y_km']     = np.zeros(len_ecef)
# leoOrb_eci['z_km']     = np.zeros(len_ecef)
# leoOrb_eci['xdot_kms'] = np.zeros(len_ecef)
# leoOrb_eci['ydot_kms'] = np.zeros(len_ecef)
# leoOrb_eci['zdot_kms'] = np.zeros(len_ecef)
#
###  Make the file if not exist



# if os.path.exists(file_IC):
#     pass
# else:
f = open(file_IC, "w")
f.write("\n")
f.close()

    
    
    
    
### Write to file
with open(file_IC, 'r+') as file:

    #### Manually write the header units
    header_units =\
                f"{'UTC'.rjust(len(str(leoOrb_ecef['date_utc'][1]))-1,' ') }"\
            +f"  {'(m)'.rjust(15,' ')}"\
            +f"  {'(m)'.rjust(15,' ')}"\
            +f"  {'(m)'.rjust(15,' ')}"\
            +f"  {'(m/s)'.rjust(15,' ')}"\
            +f"  {'(m/s)'.rjust(15,' ')}"\
            +f"  {'(m/s)'.rjust(15,' ')}"\

    #### Manually write the header field names
    header_names =\
                f"{'Date'.rjust(len(str(leoOrb_ecef['date_utc'][1]))-1,' ') }"\
            +f"  {'X'.rjust(15,' ')}"\
            +f"  {'Y'.rjust(15,' ')}"\
            +f"  {'Z'.rjust(15,' ')}"\
            +f"  {'X_dot'.rjust(15,' ')}"\
            +f"  {'Y_dot'.rjust(15,' ')}"\
            +f"  {'Z_dot'.rjust(15,' ')}"\

    #### Manually write the detailed header description
    header_meta = \
    f'''### Initial conditions file
### -----------------------
###     Satellite: Spire_083 (1804607)
###     Epoch: +start____ 2018  9 23  0 12  0.0300000 
###            +stop_____ 2018 12  9 23 43 35.9080000 
###     Last modified: {datetime.now()-timedelta(hours=7)}
###
### Source
### -------
###     leoAtt_2018-09-23T00-12-00Z.9999999.083.log
###     (long quaternion file)
###     %spire version 1.3  revision   1 2019 07 05 00:00 Spire     Spire Processing Center
###
### Contents
### --------
###     Date: (YYYY-MM-DD hh:mm:ss.ssssss) (UTC, converted from gps time)
###     pvi: Position and velocity (X, Y, Z, X_dot, Y_dot, Z_dot)
###          coordinate: ECI
###          unit: m
###
#{header_units}
#{header_names}
### %eoh
'''
    file.write(header_meta)  
    
    for indx,valdate in enumerate(leoOrb_ecef['date_utc']):
        # position vector earth fixed  ( km )
        recef = [leoOrb_ecef['x_km'][indx],  
                 leoOrb_ecef['y_km'][indx], 
                 leoOrb_ecef['z_km'][indx]]
        # velocity vector earth fixed  (km/s)
        vecef = [leoOrb_ecef['xdot_dms'][indx]*conv_dms2kms, 
                 leoOrb_ecef['ydot_dms'][indx]*conv_dms2kms,
                 leoOrb_ecef['zdot_dms'][indx]*conv_dms2kms]

        (reci, veci, _)= iau06_Call_ecef2eci(recef, vecef, None,
                                              leoOrb_ecef['date_utc'][indx].year, 
                                              leoOrb_ecef['date_utc'][indx].month, 
                                              leoOrb_ecef['date_utc'][indx].day, 
                                              leoOrb_ecef['date_utc'][indx].hour, 
                                              leoOrb_ecef['date_utc'][indx].minute, 
                                              leoOrb_ecef['date_utc'][indx].second, 
                                              calc_accel = False)
        
    #### Manually write each row of the data.
        row =   f"{leoOrb_ecef['date_utc'][indx]}"\
               +f"  {reci[0,0]*1000:15.5f}"\
               +f"  {reci[1,0]*1000:15.5f}"\
               +f"  {reci[2,0]*1000:15.5f}"\
               +f"  {veci[0,0]*1000:15.5f}"\
               +f"  {veci[1,0]*1000:15.5f}"\
               +f"  {veci[2,0]*1000:15.5f}"\
               +f"\n"
        file.write(row)

#         leoOrb_eci['x_km'][indx] = reci[0,0]
#         leoOrb_eci['y_km'][indx] = reci[1,0]
#         leoOrb_eci['z_km'][indx] = reci[2,0]
#         leoOrb_eci['xdot_kms'][indx] = veci[0,0]
#         leoOrb_eci['ydot_kms'][indx] = veci[1,0]
#         leoOrb_eci['zdot_kms'][indx] = veci[2,0]


end = time.time()
elapsed = end - start




# pr.disable()
# s = io.StringIO()
# sortby = SortKey.CUMULATIVE
# ps = pstats.Stats(pr, stream=s).sort_stats(sortby)
# ps.print_stats(20)
# print(s.getvalue())

        ### maybe we should compile the inputs to the file reading functions all at once
    
    


print(f'       indxes: 0 -',indx,'') 
print(f'       Time: ',np.round(elapsed,5),'secs') 

# print(f'       estimated time for 1 day = ', np.round( ((elapsed*33)/60), 5), 'mins')
# print(f'       Before 24.67196','secs') 
print()
# print(f'       Before 36.99681','secs')

In [ ]:
import cProfile, pstats, io
from pstats import SortKey

pr = cProfile.Profile()
pr.enable()

# iau06_Call_ecef2eci(recef, vecef, None,
#                       leoOrb_ecef['date_utc'][indx].year, 
#                       leoOrb_ecef['date_utc'][indx].month, 
#                       leoOrb_ecef['date_utc'][indx].day, 
#                       leoOrb_ecef['date_utc'][indx].hour, 
#                       leoOrb_ecef['date_utc'][indx].minute, 
#                       leoOrb_ecef['date_utc'][indx].second, 
#                       calc_accel = False)
pr.disable()
s = io.StringIO()
sortby = SortKey.CUMULATIVE
ps = pstats.Stats(pr, stream=s).sort_stats(sortby)
ps.print_stats(20)
print(s.getvalue())

In [ ]:
if 'eop_dict' in globals():   #read_once_flag==False:    
    print('hello')


In [ ]:
# globals()

In [ ]:
# conv_dms2kms = 1/10000.
# #
# len_ecef = np.shape(leoOrb_ecef['date_utc'])[0]
# #
# leoOrb_eci = {}
# leoOrb_eci['x_km']     = np.zeros(len_ecef)
# leoOrb_eci['y_km']     = np.zeros(len_ecef)
# leoOrb_eci['z_km']     = np.zeros(len_ecef)
# leoOrb_eci['xdot_kms'] = np.zeros(len_ecef)
# leoOrb_eci['ydot_kms'] = np.zeros(len_ecef)
# leoOrb_eci['zdot_kms'] = np.zeros(len_ecef)

# for indx,valdate in enumerate(leoOrb_ecef['date_utc']):
#     # position vector earth fixed  ( km )
#     recef = [leoOrb_ecef['x_km'][indx],  
#              leoOrb_ecef['y_km'][indx], 
#              leoOrb_ecef['z_km'][indx]]
#     # velocity vector earth fixed  (km/s)
#     vecef = [leoOrb_ecef['xdot_dms'][indx]*conv_dms2kms, 
#              leoOrb_ecef['ydot_dms'][indx]*conv_dms2kms,
#              leoOrb_ecef['zdot_dms'][indx]*conv_dms2kms]

#     (reci, veci, _)= iau06_Call_ecef2eci(recef, vecef, None,
#                                           leoOrb_ecef['date_utc'][indx].year, 
#                                           leoOrb_ecef['date_utc'][indx].month, 
#                                           leoOrb_ecef['date_utc'][indx].day, 
#                                           leoOrb_ecef['date_utc'][indx].hour, 
#                                           leoOrb_ecef['date_utc'][indx].minute, 
#                                           leoOrb_ecef['date_utc'][indx].second, 
#                                           calc_accel = False)
# #     listout = [action  \
# #                for item in listin]
    
# #     leoOrb_eci['x_km'][indx] = reci[0,0]
# #     leoOrb_eci['y_km'][indx] = reci[1,0]
# #     leoOrb_eci['z_km'][indx] = reci[2,0]
# #     leoOrb_eci['xdot_kms'][indx] = veci[2,0]
# #     leoOrb_eci['ydot_kms'][indx] = veci[2,0]
# #     leoOrb_eci['zdot_kms'][indx] = veci[2,0]


In [ ]:
# print(f" {pd.to_datetime(datetime(year,mon, day, hr, minute, sec))}")
# print(f"  ECEF ")
# print(f'     r [{recef[0]:14.9f}, {recef[1]:14.9f}, {recef[2]:14.9f}]' )
# print(f'     v [{vecef[0]:14.9f}, {vecef[1]:14.9f}, {vecef[2]:14.9f}]' )
# print(f"  ECI ")

# print(f'     r [{reci[0,0]:14.9f}, {reci[1,0]:14.9f}, {reci[2,0]:14.9f}]' )
# print(f'     v [{veci[0,0]:14.9f}, {veci[1,0]:14.9f}, {veci[2,0]:14.9f}]' )


In [ ]:
import sys
sys.exit()

In [ ]:
# %load_ext autoreload
# %autoreload 2
# import plotly.graph_objects as go
# from plotly.offline import plot, iplot
# from plotly.subplots import make_subplots
# import plotly.express as px

# config = dict({
#                 'displayModeBar': True,
#                 'responsive': False,
#                 'staticPlot': True,
#                 'displaylogo': False,
#                 'showTips': False,
#                 })


# fig = make_subplots(rows=1, cols=1)

# fig.add_trace(go.Scattergl(
#             x=leoOrb_ecef['date_gps'],
#             y=leoOrb_ecef['x_km'],
#                 mode='markers',
#                 opacity=1,
#                 marker=dict(size=3),
# #                 showlegend=True,
#                 ),
#                 secondary_y=False,
#                 row=1, col=1,
#                 )

# # fig.update_layout(title=''.join(coords)+' Orbit Residuals',
# #                 autosize=True,
# #                 font=dict(size=14),
# #                 legend= {'itemsizing': 'constant'})

# fig.update_layout(
#         autosize=True
# #         width=800,height=900,
#                 )
# fig.show(config=config)


In [ ]:
sys.exit(0)

# Run Pygeodyn


In [ ]:
%load_ext autoreload
%autoreload 2

from pygeodyn.PYGEODYN import Pygeodyn
from gc import collect as gc_collect





In [ ]:
# run_settings = Pygeodyn.print_input(options=False, info=False)


In [ ]:

# settings_icesat= {# Basic input settings
#                  'satellite'      : {'input': 'icesat2'},
#                  'den_model'      : {'input': 'jb2008'},
#                  'run_type'       : {'input': 'DataReduction_PCE'},
#                  'run_specifier'  : {'input': '_test_infrastruc'},
#                  'cd_model'       : {'input': 'BWDRAG'},
#                  'file_string'    : {'input': 'CD_2p5'},
#                # Force Model settings
#                   'cd_type'               : {'input':"Fixed_CD"},
#                   'cd_value'              : {'input':2.500000},
#                   'scaling_factor'        : {'input':False},
#                   'cd_adjustment_boolean' : {'input':False },
#                   'hours_between_cd_adj'  : {'input':6 },
#                # Run
#                   'step'           : {'input': 60.},
#                   #
#                   'arc'            : {'input':['2018.313',]},
#                   'epoch_start'    : {'input':["2018-11-09 00:00:00"]},
#                   'epoch_stop'     : {'input':["2018-11-10 00:00:00"]},
#                   'global_options': {'input':'pso_2018'},
#                # Request read on raw outputs
#                   'request_data'   : {'input': ['Trajectory_orbfil',
#                                                 'Density',
#                                                 'DragFile',
#                                                 'Residuals_summary']},
#               #end dict
#               }



In [ ]:
settings_SPIRE= {# Basic input settings
                 'satellite'      : {'input': 'spire83'},
                 'den_model'      : {'input': 'jb2008'},
                 'run_type'       : {'input': 'OrbitPropagation'},
                 'run_specifier'  : {'input': '_test_infrastruc'},
                 'cd_model'       : {'input': 'BWDRAG'},
                 'file_string'    : {'input': 'CD_2p3'},
               # Force Model settings
                  'cd_type'               : {'input':"Fixed_CD"},
                  'cd_value'              : {'input':2.300000},
                  'scaling_factor'        : {'input':False},
                  'cd_adjustment_boolean' : {'input':False },
                  'hours_between_cd_adj'  : {'input':6 },
               # Run
                  'step'           : {'input': 60.},
                  #
                  'arc'            : {'input':['2018.313',]},
                  'epoch_start'    : {'input':["2018-11-09 00:00:00"]},
                  'epoch_stop'     : {'input':["2018-11-10 00:00:00"]},
        # r_eci   [-5940662.04032,   -2074224.62981,    2733575.86992  ]
        # v_eci  [   -5151.36351,      -5151.36351,      -5151.36351  ]

                  'global_options': {'input':'pso_2018'},
               # Request read on raw outputs
                  'request_data'   : {'input': ['Trajectory_orbfil',
                                                'Density',
                                                'DragFile',
                                                'Residuals_summary']},
              #end dict
              }

In [ ]:
# # sat = Pygeodyn(settings_SPIRE, use_file=False)
# sat = Pygeodyn(settings_icesat, use_file=False)

# sat.run_arcs()

# icesat2.getData_BigData_lowmemory()

## Testing